In [1]:
import os
import warnings
import math
import json
import random
from copy import deepcopy
from pathlib import Path

import numpy as np
import pandas as pd
import joblib
import polars as pl
from tqdm.auto import tqdm

# Scikit-learn
from sklearn.model_selection import GroupKFold
from sklearn.model_selection import StratifiedGroupKFold, PredefinedSplit
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import f1_score

# SciPy
from scipy.spatial.transform import Rotation as R

# PyTorch
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch.optim.lr_scheduler import CosineAnnealingWarmRestarts

warnings.filterwarnings("ignore")
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# =============================================================================
# 1) CONFIG & SEED
# =============================================================================
class Config:
    RAW_DIR = Path("/kaggle/input/cmi-detect-behavior-with-sensor-data")
    IDS_DEL_PATH = Path("/kaggle/input/processdata/ids2del_prop_0.2.csv")
    EXPORT_DIR = Path("/kaggle/working/")
    BATCH_SIZE = 64
    PAD_PERCENTILE = 94
    LR_INIT = 3e-4
    WD = 3e-4
    MIXUP_ALPHA = 0.4
    EPOCHS = 220
    PATIENCE = 30
    T_0 = 25
    EMA_DECAY = 0.99
    ACC_COLS = ["acc_x", "acc_y", "acc_z"]
    ROT_COLS = ["rot_w", "rot_x", "rot_y", "rot_z"]
    SEED = 42

os.makedirs(Config.EXPORT_DIR, exist_ok=True)

def set_seed(seed=42):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

set_seed(Config.SEED)

# =============================================================================
# 2) LOSS / AUGS / UTILITIES
# =============================================================================
class FocalLoss(nn.Module):
    """
    Focal loss cho soft labels (mixup). Tính trên log_softmax.
    """
    def __init__(self, alpha=0.25, gamma=2.0, reduction="mean"):
        super().__init__()
        self.alpha = alpha
        self.gamma = gamma
        self.reduction = reduction

    def forward(self, inputs, targets):
        # inputs: logits (N, C); targets: soft labels (N, C)
        logp = F.log_softmax(inputs, dim=1)
        p = logp.exp()
        ce = -(targets * logp)                   # per-class CE
        focal = self.alpha * (1 - p) ** self.gamma * ce
        loss = focal.sum(dim=1)                  # sum over classes
        return loss.mean() if self.reduction == "mean" else loss.sum()

def handle_quaternion_missing_values(rot_data: np.ndarray) -> np.ndarray:
    rot_cleaned = rot_data.copy()
    for i in range(len(rot_data)):
        row = rot_data[i]
        missing_count = np.isnan(row).sum()
        if missing_count == 0:
            norm = np.linalg.norm(row)
            rot_cleaned[i] = row / norm if norm > 1e-8 else [1.0, 0.0, 0.0, 0.0]
        elif missing_count == 1:
            missing_idx = np.where(np.isnan(row))[0][0]
            valid_values = row[~np.isnan(row)]
            sum_squares = np.sum(valid_values**2)
            if sum_squares <= 1.0:
                missing_value = np.sqrt(max(0, 1.0 - sum_squares))
                if i > 0 and not np.isnan(rot_cleaned[i-1, missing_idx]) and rot_cleaned[i-1, missing_idx] < 0:
                    missing_value = -missing_value
                rot_cleaned[i, missing_idx] = missing_value
            else:
                rot_cleaned[i] = [1.0, 0.0, 0.0, 0.0]
        else:
            rot_cleaned[i] = [1.0, 0.0, 0.0, 0.0]
    return rot_cleaned

def calculate_angular_velocity_from_quat(rot_data, time_delta=1/200):
    quat_values = rot_data[:, [1, 2, 3, 0]] if rot_data.shape[1] == 4 else rot_data
    num_samples = quat_values.shape[0]
    angular_vel = np.zeros((num_samples, 3))
    for i in range(num_samples - 1):
        q_t, q_t_plus_dt = quat_values[i], quat_values[i+1]
        if np.any(np.isnan(q_t)) or np.any(np.isnan(q_t_plus_dt)):
            continue
        try:
            rot_t, rot_t_plus_dt = R.from_quat(q_t), R.from_quat(q_t_plus_dt)
            delta_rot = rot_t.inv() * rot_t_plus_dt
            angular_vel[i, :] = delta_rot.as_rotvec() / time_delta
        except ValueError:
            pass
    return angular_vel

def calculate_angular_distance(rot_data):
    quat_values = rot_data[:, [1, 2, 3, 0]] if rot_data.shape[1] == 4 else rot_data
    num_samples = quat_values.shape[0]
    angular_dist = np.zeros(num_samples)
    for i in range(num_samples - 1):
        q1, q2 = quat_values[i], quat_values[i+1]
        if np.any(np.isnan(q1)) or np.any(np.isnan(q2)):
            continue
        try:
            r1, r2 = R.from_quat(q1), R.from_quat(q2)
            angle = np.linalg.norm((r1.inv() * r2).as_rotvec())
            angular_dist[i] = angle
        except ValueError:
            pass
    return angular_dist

def remove_gravity_from_acc(acc_data, rot_data):
    acc_values = acc_data.values if isinstance(acc_data, pd.DataFrame) else acc_data
    quat_values = rot_data.values if isinstance(rot_data, pd.DataFrame) else rot_data
    quat_scipy = quat_values[:, [1, 2, 3, 0]]
    num_samples = acc_values.shape[0]
    linear_accel = np.zeros_like(acc_values)
    gravity_world = np.array([0, 0, 9.81])
    for i in range(num_samples):
        if np.any(np.isnan(quat_scipy[i])):
            linear_accel[i, :] = acc_values[i, :]
            continue
        try:
            rotation = R.from_quat(quat_scipy[i])
            gravity_sensor_frame = rotation.apply(gravity_world, inverse=True)
            linear_accel[i, :] = acc_values[i, :] - gravity_sensor_frame
        except ValueError:
            linear_accel[i, :] = acc_values[i, :]
    return linear_accel

def add_features(df: pd.DataFrame) -> pd.DataFrame:
    df["acc_mag"] = np.linalg.norm(df[Config.ACC_COLS].values, axis=1)
    df["acc_mag_jerk"] = df.groupby("sequence_id")["acc_mag"].diff().fillna(0)
    df["jerk_x"], df["jerk_y"], df["jerk_z"] = np.gradient(df["acc_x"]), np.gradient(df["acc_y"]), np.gradient(df["acc_z"])
    df["jerk_magnitude"] = np.linalg.norm(df[["jerk_x", "jerk_y", "jerk_z"]].values, axis=1)

    window = 20
    for _, g in df.groupby("sequence_id"):
        df.loc[g.index, "acc_xy_corr"] = g["acc_x"].rolling(window, min_periods=1).corr(g["acc_y"]).fillna(0)
        df.loc[g.index, "acc_xz_corr"] = g["acc_x"].rolling(window, min_periods=1).corr(g["acc_z"]).fillna(0)
        df.loc[g.index, "acc_yz_corr"] = g["acc_y"].rolling(window, min_periods=1).corr(g["acc_z"]).fillna(0)

    df["rot_angle"] = 2 * np.arccos(df["rot_w"].clip(-1, 1))
    df["rot_angle_vel"] = df.groupby("sequence_id")["rot_angle"].diff().fillna(0)

    rot_numpy = df[Config.ROT_COLS].to_numpy()
    angular_vel = calculate_angular_velocity_from_quat(rot_numpy)
    angular_dist = calculate_angular_distance(rot_numpy)
    df[["angular_vel_x", "angular_vel_y", "angular_vel_z"]] = angular_vel
    df["angular_distance"] = angular_dist
    df["angular_vel_magnitude"] = np.linalg.norm(angular_vel, axis=1)

    linear_accel = remove_gravity_from_acc(df[Config.ACC_COLS], df[Config.ROT_COLS])
    df[["acc_x2", "acc_y2", "acc_z2"]] = linear_accel
    df["acc_mag2"] = np.linalg.norm(linear_accel, axis=1)
    df["acc_mag_jerk2"] = df.groupby("sequence_id")["acc_mag2"].diff().fillna(0)
    df["jerk_x2"], df["jerk_y2"], df["jerk_z2"] = np.gradient(df["acc_x2"]), np.gradient(df["acc_y2"]), np.gradient(df["acc_z2"])
    df["jerk_magnitude2"] = np.linalg.norm(df[["jerk_x2", "jerk_y2", "jerk_z2"]].values, axis=1)

    for _, g in df.groupby("sequence_id"):
        df.loc[g.index, "acc_xy_corr2"] = g["acc_x2"].rolling(window, min_periods=1).corr(g["acc_y2"]).fillna(0)
        df.loc[g.index, "acc_xz_corr2"] = g["acc_x2"].rolling(window, min_periods=1).corr(g["acc_z2"]).fillna(0)
        df.loc[g.index, "acc_yz_corr2"] = g["acc_y2"].rolling(window, min_periods=1).corr(g["acc_z2"]).fillna(0)

    df.replace([np.inf, -np.inf], 0, inplace=True)
    df.fillna(0, inplace=True)
    return df

def pad_sequences(sequences: list, maxlen: int, padding: str="pre", truncating: str="pre", dtype: str="float32") -> np.ndarray:
    n_samples = len(sequences)
    sample_shape = tuple()
    for s in sequences:
        if len(s) > 0:
            sample_shape = np.asarray(s).shape[1:]
            break
    x = np.zeros((n_samples, maxlen) + sample_shape, dtype=dtype)
    for idx, s in enumerate(sequences):
        if len(s) == 0:
            continue
        s_np = np.asarray(s, dtype=dtype)
        if truncating == "pre":
            s_np = s_np[-maxlen:]
        else:
            s_np = s_np[:maxlen]
        trunc = s_np.shape[0]
        if padding == "pre":
            x[idx, -trunc:] = s_np
        else:
            x[idx, :trunc] = s_np
    return x

def to_categorical(y, num_classes=None):
    y = np.array(y, dtype="int")
    if not num_classes:
        num_classes = np.max(y) + 1
    return np.eye(num_classes)[y]

def preprocess_left_handed_pd(df_pd: pd.DataFrame, demo_pd: pd.DataFrame) -> pd.DataFrame:
    pl_df = pl.DataFrame(df_pd)
    pl_demo = pl.DataFrame(demo_pd)
    l_subjs = pl_demo.filter(pl.col("handedness") == 0)["subject"].to_list()
    r_tr = pl_df.filter(~pl.col("subject").is_in(l_subjs))
    l_tr = pl_df.filter(pl.col("subject").is_in(l_subjs))
    if l_tr.shape[0] == 0:
        return r_tr.to_pandas()

    l_tr = l_tr.with_columns(-pl.col("acc_y"))
    l_tr = l_tr.with_columns(-pl.col("acc_z"))
    rot_np = l_tr.select(Config.ROT_COLS).to_numpy()
    rot_scipy = rot_np[:, [1, 2, 3, 0]]
    r = R.from_quat(rot_scipy)
    tmp = r.as_euler("xyz")
    tmp[:, 1] = -tmp[:, 1]
    tmp[:, 2] = -tmp[:, 2]
    r = R.from_euler("xyz", tmp)
    tmp = r.as_quat()
    l_tr = l_tr.with_columns(pl.DataFrame(tmp, schema=["rot_x", "rot_y", "rot_z", "rot_w"]))
    pl_df2 = pl.concat([r_tr, l_tr]).sort(by="row_id")
    return pl_df2.to_pandas()

# =============================================================================
# 3) AUGMENTATIONS
# =============================================================================
class SignalTransform:
    def __init__(self, p=0.5): self.p = p
    def __call__(self, y: np.ndarray):
        if np.random.rand() < self.p: return self.apply(y)
        return y
    def apply(self, y: np.ndarray): raise NotImplementedError

class TimeStretch(SignalTransform):
    def __init__(self, max_rate=1.5, min_rate=0.5, p=0.5):
        super().__init__(p); self.max_rate, self.min_rate = max_rate, min_rate
    def apply(self, x: np.ndarray):
        rate = np.random.uniform(self.min_rate, self.max_rate)
        L = x.shape[0]; L_new = int(L / rate)
        orig_idx = np.linspace(0, L - 1, L)
        new_idx = np.linspace(0, L - 1, L_new)
        stretched = np.stack([np.interp(new_idx, orig_idx, x[:, i]) for i in range(x.shape[1])], axis=1)
        if L_new < L:
            padded = np.zeros((L, x.shape[1]), dtype=stretched.dtype)
            padded[-L_new:, :] = stretched
            return padded
        return stretched[-L:, :]

class TimeShift(SignalTransform):
    def __init__(self, p=0.5, max_shift_pct=0.25):
        super().__init__(p); self.max_shift_pct = max_shift_pct
    def apply(self, x: np.ndarray):
        L = x.shape[0]
        shift = np.random.randint(-int(L * self.max_shift_pct), int(L * self.max_shift_pct) + 1)
        augmented = np.roll(x, shift, axis=0)
        if shift > 0: augmented[:shift, :] = 0
        elif shift < 0: augmented[shift:, :] = 0
        return augmented

class SignalPermutation(SignalTransform):
    def __init__(self, p=0.5):
        super().__init__(p)
    def apply(self, x: np.ndarray):
        augmented = x.copy()
        # acc: cột 0..2
        perm_acc = np.random.permutation(3)
        augmented[:, 0:3] = augmented[:, perm_acc]
        # gyro: ví dụ ở cột 15..17
        if x.shape[1] > 17:
            perm_gyro = np.random.permutation(3)
            original = augmented[:, 15:18].copy()
            augmented[:, 15:18] = original[:, perm_gyro]
        return augmented

class Compose:
    def __init__(self, transforms: list): self.transforms = transforms
    def __call__(self, y: np.ndarray):
        for trns in self.transforms: y = trns(y)
        return y


# --- Pyramid Temporal Feature (PTF) ---
class PyramidTemporalFeature(nn.Module):
    """
    Module trích xuất đặc trưng theo nhiều tần suất thời gian khác nhau.
    Tương tự FPN nhưng dùng nhiều Conv1D kernel size khác nhau để nắm bắt pattern ngắn & dài.
    """
    def __init__(self, in_channels, out_channels, kernel_sizes=[3, 5, 7]):
        super().__init__()
        self.branches = nn.ModuleList([
            nn.Sequential(
                nn.Conv1d(in_channels, out_channels, kernel_size=k, padding=k//2),
                nn.BatchNorm1d(out_channels),
                nn.ReLU(inplace=True)
            )
            for k in kernel_sizes
        ])
        # Gộp lại các scale
        self.fuse = nn.Conv1d(out_channels * len(kernel_sizes), out_channels, kernel_size=1)

    def forward(self, x):
        # x: [B, C, T]
        features = [branch(x) for branch in self.branches]  # nhiều scale thời gian
        concat = torch.cat(features, dim=1)  # ghép theo kênh
        out = self.fuse(concat)              # hợp nhất lại
        return out                           # [B, out_channels, T]
# =============================================================================
# 4) DATASET
# =============================================================================
class MixupDataset(Dataset):
    def __init__(self, X, y, transforms, alpha=0.2, mode="train"):
        self.X, self.y = X, y
        self.transforms = transforms
        self.alpha, self.mode = alpha, mode
    def __len__(self): return len(self.X)
    def __getitem__(self, idx):
        X, y = self.X[idx].copy(), self.y[idx].copy()
        if self.mode == "train":
            if self.alpha > 0:
                lam = np.random.beta(self.alpha, self.alpha)
                idx2 = np.random.randint(len(self.X))
                X = lam * X + (1 - lam) * self.X[idx2]
                y = lam * y + (1 - lam) * self.y[idx2]
            X = self.transforms(X)
        return torch.FloatTensor(X), torch.FloatTensor(y)

# =============================================================================
# 5) MODEL
# =============================================================================
class SEBlock(nn.Module):
    def __init__(self, channel, reduction=8):
        super().__init__()
        self.avg_pool = nn.AdaptiveAvgPool1d(1)
        self.fc = nn.Sequential(
            nn.Linear(channel, channel // reduction), nn.ReLU(inplace=True),
            nn.Linear(channel // reduction, channel), nn.Sigmoid())
    def forward(self, x):
        b, c, _ = x.size()
        y = self.avg_pool(x).view(b, c)
        y = self.fc(y).view(b, c, 1)
        return x * y.expand_as(x)

class ResidualSEBlock(nn.Module):
    def __init__(self, in_channels, out_channels, kernel_size, drop=0.3):
        super().__init__()
        self.conv1 = nn.Conv1d(in_channels, out_channels, kernel_size, padding="same", bias=False)
        self.bn1 = nn.BatchNorm1d(out_channels)
        self.conv2 = nn.Conv1d(out_channels, out_channels, kernel_size, padding="same", bias=False)
        self.bn2 = nn.BatchNorm1d(out_channels)
        self.se = SEBlock(out_channels)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(drop)
        self.pool = nn.MaxPool1d(2)
        self.shortcut = nn.Sequential(
            nn.Conv1d(in_channels, out_channels, 1, bias=False),
            nn.BatchNorm1d(out_channels)
        ) if in_channels != out_channels else nn.Identity()
    def forward(self, x):
        identity = self.shortcut(x)
        out = self.relu(self.bn1(self.conv1(x)))
        out = self.se(self.bn2(self.conv2(out)))
        out = self.dropout(self.pool(self.relu(out + identity)))
        return out

class AttentionLayer(nn.Module):
    def __init__(self, hidden_dim): super().__init__(); self.attn = nn.Sequential(nn.Linear(hidden_dim, 1), nn.Tanh())
    def forward(self, x):
        weights = F.softmax(self.attn(x).squeeze(-1), dim=1).unsqueeze(-1)
        return torch.sum(x * weights, dim=1)

class CrossAttention(nn.Module):
    def __init__(self, feature_dim, num_heads=8, dropout=0.1):
        super().__init__()
        self.feature_dim = feature_dim
        self.num_heads = num_heads
        self.head_dim = feature_dim // num_heads
        assert feature_dim % num_heads == 0, "feature_dim must be divisible by num_heads"
        self.q_linear = nn.Linear(feature_dim, feature_dim, bias=False)
        self.k_linear = nn.Linear(feature_dim, feature_dim, bias=False)
        self.v_linear = nn.Linear(feature_dim, feature_dim, bias=False)
        self.out_linear = nn.Linear(feature_dim, feature_dim)
        self.dropout = nn.Dropout(dropout)
        self.layer_norm = nn.LayerNorm(feature_dim)
    def forward(self, query_branch, key_value_branches):
        B, T, C = query_branch.shape
        Q = self.q_linear(query_branch)
        all_kv = torch.cat(key_value_branches, dim=1)
        K = self.k_linear(all_kv)
        V = self.v_linear(all_kv)
        Q = Q.view(B, T, self.num_heads, self.head_dim).transpose(1, 2)
        K = K.view(B, -1, self.num_heads, self.head_dim).transpose(1, 2)
        V = V.view(B, -1, self.num_heads, self.head_dim).transpose(1, 2)
        scores = torch.matmul(Q, K.transpose(-2, -1)) / math.sqrt(self.head_dim)
        attn_weights = F.softmax(scores, dim=-1)
        attn_weights = self.dropout(attn_weights)
        attn_output = torch.matmul(attn_weights, V)
        attn_output = attn_output.transpose(1, 2).contiguous().view(B, T, C)
        output = self.out_linear(attn_output)
        output = self.layer_norm(query_branch + output)
        return output

class IMUCrossAttentionFusion(nn.Module):
    def __init__(self, feature_dim=256, num_heads=8, dropout=0.1):
        super().__init__()
        self.cross_attn1 = CrossAttention(feature_dim, num_heads, dropout)
        self.cross_attn2 = CrossAttention(feature_dim, num_heads, dropout)
        self.cross_attn3 = CrossAttention(feature_dim, num_heads, dropout)
    def forward(self, imu1, imu2, imu3):
        e1 = self.cross_attn1(imu1, [imu2, imu3])
        e2 = self.cross_attn2(imu2, [imu1, imu3])
        e3 = self.cross_attn3(imu3, [imu1, imu2])
        return e1, e2, e3

class IMUCrossAttentionModel_PTF(nn.Module):
    def __init__(self, imu_dim, n_classes):
        super().__init__()
        self.imu_dim = imu_dim

        # --- 3 nhánh CNN backbone cho dữ liệu IMU ---
        self.imu_branch1 = nn.Sequential(
            ResidualSEBlock(12, 128, 3),
            ResidualSEBlock(128, 256, 5)
        )
        self.imu_branch2 = nn.Sequential(
            ResidualSEBlock(11, 128, 3),
            ResidualSEBlock(128, 256, 5)
        )
        self.imu_branch3 = nn.Sequential(
            ResidualSEBlock(12, 128, 3),
            ResidualSEBlock(128, 256, 5)
        )

        # --- Pyramid Temporal Feature cho mỗi nhánh ---
        self.ptf1 = PyramidTemporalFeature(256, 128)
        self.ptf2 = PyramidTemporalFeature(256, 128)
        self.ptf3 = PyramidTemporalFeature(256, 128)

        # --- Cross attention fusion ---
        self.cross_attention_fusion = IMUCrossAttentionFusion(feature_dim=128)

        # --- BiLSTM + attention + FC ---
        self.bilstm = nn.LSTM(128 * 3, 512, bidirectional=True, batch_first=True)
        self.attention = AttentionLayer(1024)
        self.fc = nn.Linear(1024, n_classes)
    
    def forward(self, x):
        imu = x[:, :, :self.imu_dim]

        # tách dữ liệu IMU cho 3 nhánh (tuỳ theo cấu trúc cảm biến)
        imu1 = self.imu_branch1(imu[:, :, :12].transpose(1, 2))     # [B, C, T]
        imu2 = self.imu_branch2(imu[:, :, 12:23].transpose(1, 2))
        imu3 = self.imu_branch3(imu[:, :, 23:].transpose(1, 2))
        
        # --- Trích đặc trưng đa tần số thời gian ---
        imu1_ptf = self.ptf1(imu1).transpose(1, 2)
        imu2_ptf = self.ptf2(imu2).transpose(1, 2)
        imu3_ptf = self.ptf3(imu3).transpose(1, 2)

        # --- Cross attention fusion giữa 3 nhánh ---
        imu1, imu2, imu3 = self.cross_attention_fusion(imu1_ptf, imu2_ptf, imu3_ptf)
    
        # --- Ghép & đưa qua BiLSTM ---
        merged = torch.cat((imu1, imu2, imu3), dim=2)
        lstm_out, _ = self.bilstm(merged)

        # --- Attention + phân lớp ---
        attended = self.attention(lstm_out)
        return self.fc(attended)

class ModelEMA(nn.Module):
    def __init__(self, model, decay=0.99, device=None):
        super().__init__()
        self.module = deepcopy(model)
        self.module.eval()
        self.decay = decay
        self.device = device
        if self.device:
            self.module.to(device=device)
    def _update(self, model, update_fn):
        with torch.no_grad():
            for ema_v, model_v in zip(self.module.state_dict().values(), model.state_dict().values()):
                if self.device:
                    model_v = model_v.to(device=self.device)
                ema_v.copy_(update_fn(ema_v, model_v))
    def update(self, model): self._update(model, update_fn=lambda e, m: self.decay * e + (1. - self.decay) * m)
    def set(self, model): self._update(model, update_fn=lambda e, m: m)

# =============================================================================
# 6) TRAIN ONE FOLD
# =============================================================================
def train_single_fold(df_train, df_val, imu_cols, le, fold_num):
    print(f"\n========== Begin Fold {fold_num} | Train IMU Cross-Attention ==========")

    # pad_len theo percentile của fold
    seq_lengths = [len(group) for _, group in df_train.groupby("sequence_id")]
    pad_len = int(np.percentile(seq_lengths, Config.PAD_PERCENTILE))

    # build sequences
    X_tr_list = [seq[imu_cols].to_numpy() for _, seq in df_train.groupby("sequence_id")]
    y_tr_int  = [seq["gesture_int"].iloc[0] for _, seq in df_train.groupby("sequence_id")]
    X_tr = pad_sequences(X_tr_list, maxlen=pad_len)
    y_tr = to_categorical(y_tr_int, num_classes=len(le.classes_))

    X_va_list = [seq[imu_cols].to_numpy() for _, seq in df_val.groupby("sequence_id")]
    y_va_int  = [seq["gesture_int"].iloc[0] for _, seq in df_val.groupby("sequence_id")]
    X_va = pad_sequences(X_va_list, maxlen=pad_len)
    y_va = to_categorical(y_va_int, num_classes=len(le.classes_))

    model = IMUCrossAttentionModel_PTF(len(imu_cols), len(le.classes_)).to(device)
    print(f"Model has {sum(p.numel() for p in model.parameters()) / 1e6:.1f}M parameters.")

    ema_model = ModelEMA(model, decay=Config.EMA_DECAY, device=device)
    optimizer = torch.optim.Adam(model.parameters(), lr=Config.LR_INIT, weight_decay=Config.WD)
    criterion = FocalLoss()
    scheduler = CosineAnnealingWarmRestarts(optimizer, T_0=Config.T_0)

    transforms = Compose([TimeShift(p=0.35, max_shift_pct=0.25),
                          TimeStretch(p=0.35),
                          SignalPermutation(p=0.5)])

    train_dataset = MixupDataset(X_tr, y_tr, alpha=Config.MIXUP_ALPHA, mode="train", transforms=transforms)
    train_loader = DataLoader(train_dataset, batch_size=Config.BATCH_SIZE, shuffle=True, drop_last=True)
    val_dataset = MixupDataset(X_va, y_va, alpha=0, mode="valid", transforms=Compose([]))
    val_loader = DataLoader(val_dataset, batch_size=Config.BATCH_SIZE)

    best_val_loss = float('inf')
    patience_counter = 0
    model_path = Config.EXPORT_DIR / f"model_best_fold_{fold_num}.pt"

    for epoch in range(Config.EPOCHS):
        model.train()
        train_loss = 0.0
        pbar = tqdm(train_loader, desc=f"Fold {fold_num} | Epoch {epoch+1}/{Config.EPOCHS}")
        for batch_X, batch_y in pbar:
            batch_X, batch_y = batch_X.to(device), batch_y.to(device)
            optimizer.zero_grad()
            outputs = model(batch_X)
            loss = criterion(outputs, batch_y)
            loss.backward()
            optimizer.step()
            train_loss += loss.item()
            ema_model.update(model)
            pbar.set_postfix(loss=float(loss.item()))
        train_loss /= len(train_loader)
        scheduler.step()

        # validation loss
        val_loss = 0.0
        ema_model.module.eval()
        with torch.no_grad():
            for batch_X, batch_y in val_loader:
                out = ema_model.module(batch_X.to(device))
                val_loss += criterion(out, batch_y.to(device)).item()
        val_loss /= len(val_loader)

        print(f"Fold {fold_num} | Epoch [{epoch+1}/{Config.EPOCHS}] Train {train_loss:.4f} | Val {val_loss:.4f}")

        if val_loss < best_val_loss:
            best_val_loss = val_loss
            patience_counter = 0
            torch.save(ema_model.module.state_dict(), model_path)
            print(f"-> Improved Val Loss {best_val_loss:.4f}. Saved to {model_path}")
        else:
            patience_counter += 1
            if patience_counter >= Config.PATIENCE:
                print(f"Early stopping after {epoch+1} epochs.")
                break

    ema_model.module.eval()
    va_probs = []
    with torch.no_grad():
        for batch_X, _ in DataLoader(val_dataset, batch_size=Config.BATCH_SIZE):
            logits = ema_model.module(batch_X.to(device))
            probs = torch.softmax(logits, dim=1).cpu().numpy()
            va_probs.append(probs)
    va_probs = np.vstack(va_probs)                      # (N_val, C)
    va_preds = va_probs.argmax(1)
    oof_f1 = f1_score(y_va_int, va_preds, average="macro")

    with open(Config.EXPORT_DIR / f"oof_score_fold_{fold_num}.json", "w") as f:
        json.dump({"fold": fold_num, "macro_f1": float(oof_f1), "val_loss": float(best_val_loss)}, f)

    print(f"Fold {fold_num} done. Best Val Loss: {best_val_loss:.4f} | OOF macro-F1: {oof_f1:.4f}")
    return pad_len

# =============================================================================
# 7) MAIN WORKFLOW 
# =============================================================================
def main():
    print("Load data...")
    df = pd.read_csv(Config.RAW_DIR / "train.csv")
    dem = pd.read_csv(Config.RAW_DIR / "train_demographics.csv")

    if Config.IDS_DEL_PATH.exists():
        ids2del = pd.read_csv(Config.IDS_DEL_PATH)
        df = df[~df["sequence_id"].isin(ids2del["sequence_id"])]
        print("Đã loại bỏ các sequence nhiễu từ ids2del.")
 
    print("✅ Removed sequences successfully.")

    # labels
    le = LabelEncoder()
    df["gesture_int"] = le.fit_transform(df["gesture"])
    print("Quaternions & NaNs...")
    df[Config.ROT_COLS] = handle_quaternion_missing_values(df[Config.ROT_COLS].to_numpy())
    df = pd.concat([seq.ffill().bfill().fillna(0) for _, seq in df.groupby("sequence_id")], axis=0)

    df = preprocess_left_handed_pd(df, dem)

    print("Adding features...")
    df = add_features(df)

    meta_cols = {"gesture", "gesture_int", "sequence_type", "behavior", "orientation",
                 "row_id", "subject", "phase", "sequence_id", "sequence_counter",
                 "handedness", "height", "weight", "age"}
    imu_cols = [c for c in df.columns if c not in meta_cols and not (c.startswith("thm_") or c.startswith("tof_"))]
    print(f"Sử dụng {len(imu_cols)} IMU features.")

    sgkf = StratifiedGroupKFold(n_splits=5, shuffle=True, random_state=42)
    
    for fold, (tr_idx, va_idx) in enumerate(sgkf.split(df, y=df["gesture_int"], groups=df["subject"]),start=1):
        print(f"\n--- Processing Fold {fold} ---")
        df_train = df.iloc[tr_idx].copy()
        df_val   = df.iloc[va_idx].copy()

        pad_len = train_single_fold(df_train, df_val, imu_cols, le, fold_num=fold)
        prep = {
            "transformer": None,
            "categories": list(le.classes_),
            "features": imu_cols,
            "max_length": pad_len,
            "fold": fold
        }
        joblib.dump(prep, Config.EXPORT_DIR / f"prep_fold_{fold}.joblib")
        print(f"Saved prep_fold_{fold}.joblib")

    print("\n Hoàn tất 5-fold CV.")
   
if __name__ == "__main__":
    main()


Using device: cuda
Load data...
Đã loại bỏ các sequence nhiễu từ ids2del.
✅ Removed sequences successfully.
Quaternions & NaNs...
Adding features...
Sử dụng 35 IMU features.

--- Processing Fold 1 ---

========== Begin Fold 1 | Train IMU Cross-Attention ==========
Model has 7.3M parameters.


Fold 1 | Epoch 1/220:   0%|          | 0/102 [00:00<?, ?it/s]

Fold 1 | Epoch [1/220] Train 0.4609 | Val 0.4408
-> Improved Val Loss 0.4408. Saved to /kaggle/working/model_best_fold_1.pt


Fold 1 | Epoch 2/220:   0%|          | 0/102 [00:00<?, ?it/s]

Fold 1 | Epoch [2/220] Train 0.3378 | Val 0.2935
-> Improved Val Loss 0.2935. Saved to /kaggle/working/model_best_fold_1.pt


...

Fold 5 | Epoch [133/220] Train 0.1835 | Val 0.1364


Fold 5 | Epoch 134/220:   0%|          | 0/101 [00:00<?, ?it/s]

Fold 5 | Epoch [134/220] Train 0.1797 | Val 0.1361


Fold 5 | Epoch 135/220:   0%|          | 0/101 [00:00<?, ?it/s]

Fold 5 | Epoch [135/220] Train 0.1795 | Val 0.1374
Early stopping after 135 epochs.
Fold 5 done. Best Val Loss: 0.1338 | OOF macro-F1: 0.7422
Saved prep_fold_5.joblib

 Hoàn tất 5-fold CV.
